In [1]:
import numpy as np
import pandas as pd
from tqdm import tqdm
pd.set_option('max_columns', 1200)
pd.set_option('max_rows', 100)

In [2]:
df = pd.read_csv('КР/Quarterly_Fin_Table_Target.csv', sep=';')
df

ticker   period ind_template REIT         isDirect  Revenue per Share  \
0         HTD  2004-03          NaN  NaN              NaN                NaN   
1         HTD  2004-04          NaN  NaN              NaN                NaN   
2         HTD  2004-05          NaN  NaN              NaN                NaN   
3         HTD  2004-06          NaN  NaN              NaN                NaN   
4         HTD  2004-07          NaN  NaN              NaN                NaN   
...       ...      ...          ...  ...              ...                ...   
311545    YUM  2021-07          NaN  NaN              NaN                NaN   
311546    YUM  2021-08          NaN  NaN              NaN                NaN   
311547    YUM  2021-09            N    N  Indirect Method              5.318   
311548    YUM  2021-10          NaN  NaN              NaN                NaN   
311549    YUM  2021-11          NaN  NaN              NaN                NaN   

        Earnings per Share (Diluted)  EPS without NRI  \
0                                NaN              NaN   
1                                NaN              NaN   
2                                NaN              NaN   
3                                NaN              NaN   
4                                NaN              NaN   
...                              ...              ...   
311545                           NaN              NaN   
311546                           NaN              NaN   
311547                          1.75             1.75   
311548                           NaN              NaN   
311549                           NaN              NaN   

        Owner Earnings per Share (TTM)  Free Cash Flow per Share  \
0                                  NaN                       NaN   
1                                  NaN                       NaN   
2                                  NaN                       NaN   
3                                  NaN                       NaN   
4                                  NaN                       NaN   
...                                ...                       ...   
311545                             NaN                       NaN   
311546                             NaN                       NaN   
311547                           4.648                      1.54   
311548                             NaN                       NaN   
311549                             NaN                       NaN   

        Operating Cash Flow per Share  Cash per Share  Dividends per Share  \
0                                 NaN             NaN                  NaN   
1                                 NaN             NaN                  NaN   
2                                 NaN             NaN                  NaN   
3                                 NaN             NaN                  NaN   
4                                 NaN             NaN                  NaN   
...                               ...             ...                  ...   
311545                            NaN             NaN                  NaN   
311546                            NaN             NaN                  NaN   
311547                          1.719           3.405                  0.5   
311548                            NaN             NaN                  NaN   
311549                            NaN             NaN                  NaN   

        Book Value per Share  Tangible Book per Share  Total Debt per Share  \
0                        NaN                      NaN                   NaN   
1                        NaN                      NaN                   NaN   
2                        NaN                      NaN                   NaN   
3                        NaN                      NaN                   NaN   
4                        NaN                      NaN                   NaN   
...                      ...                      ...                   ...   
311545                   NaN                      NaN 

#### Добавляем пропущенные месяцы:

In [3]:
df['period'] = pd.to_datetime([i+'-01' for i in df['period']])
tickers = df['ticker'].unique()

In [4]:
%%time

full_dates = set(pd.date_range(start=df['period'].min(), end=df['period'].max(), freq='MS'))
tick_dates_missed = dict()
for t in tqdm(tickers):
    cur_dates = set(df.loc[df['ticker'] == t, 'period'])
    missed_dates = np.array(list(full_dates - cur_dates))
    if missed_dates.size:
        tick_dates_missed[t] = missed_dates[(missed_dates > min(cur_dates)) & (missed_dates < max(cur_dates))]
    
# tick_dates_missed

100%|███████████████████████████████████████| 1490/1490 [00:21<00:00, 70.51it/s]

CPU times: user 21 s, sys: 226 ms, total: 21.2 s
Wall time: 21.2 s


In [5]:
%%time

n_rows = 0
rows = np.full(df.shape[1], np.nan)

for t in tqdm(tick_dates_missed.keys()):
    n_rows += tick_dates_missed[t].size
    tick = np.full(tick_dates_missed[t].size, t)
    period = tick_dates_missed[t]
    other = np.full((tick_dates_missed[t].size, df.shape[1]-2), np.nan)
    row_add = np.hstack((np.vstack((tick, period)).T, other))
    rows = np.vstack((rows, row_add))
    

n_rows, rows.shape

100%|███████████████████████████████████████| 1485/1485 [00:57<00:00, 25.67it/s]

CPU times: user 51.7 s, sys: 6.41 s, total: 58.1 s
Wall time: 57.9 s


(6363, (6364, 1152))

In [6]:
%%time
new_df = pd.DataFrame(
    np.vstack((df.values, rows[1:])
             ), columns=df.columns).sort_values(by=['ticker', 'period']).reset_index(drop=True)
new_df

CPU times: user 2min 20s, sys: 4min 9s, total: 6min 29s
Wall time: 8min 53s


ticker     period ind_template REIT         isDirect Revenue per Share  \
0         AAL 2005-10-01          NaN  NaN              NaN               NaN   
1         AAL 2005-11-01          NaN  NaN              NaN               NaN   
2         AAL 2005-12-01            N    N  Indirect Method            79.612   
3         AAL 2006-01-01          NaN  NaN              NaN               NaN   
4         AAL 2006-02-01          NaN  NaN              NaN               NaN   
...       ...        ...          ...  ...              ...               ...   
317908   ZYNE 2021-07-01          NaN  NaN              NaN               NaN   
317909   ZYNE 2021-08-01          NaN  NaN              NaN               NaN   
317910   ZYNE 2021-09-01          NaN  NaN              NaN               NaN   
317911   ZYNE 2021-10-01          NaN  NaN              NaN               NaN   
317912   ZYNE 2021-11-01          NaN  NaN              NaN               NaN   

       Earnings per Share (Diluted) EPS without NRI  \
0                               NaN             NaN   
1                               NaN             NaN   
2                            -9.639          -9.639   
3                               NaN             NaN   
4                               NaN             NaN   
...                             ...             ...   
317908                          NaN             NaN   
317909                          NaN             NaN   
317910                          NaN             NaN   
317911                          NaN             NaN   
317912                          NaN             NaN   

       Owner Earnings per Share (TTM) Free Cash Flow per Share  \
0                                 NaN                      NaN   
1                                 NaN                      NaN   
2                              -3.918                   -1.587   
3                                 NaN                      NaN   
4                                 NaN                      NaN   
...                               ...                      ...   
317908                            NaN                      NaN   
317909                            NaN                      NaN   
317910                            NaN                      NaN   
317911                            NaN                      NaN   
317912                            NaN                      NaN   

       Operating Cash Flow per Share Cash per Share Dividends per Share  \
0                                NaN            NaN                 NaN   
1                                NaN            NaN                 NaN   
2                             -0.123         55.882                 0.0   
3                                NaN            NaN                 NaN   
4                                NaN            NaN                 NaN   
...                              ...            ...                 ...   
317908                           NaN            NaN                 NaN   
317909                           NaN            NaN                 NaN   
317910                           NaN            NaN                 NaN   
317911                           NaN            NaN                 NaN   
317912                           NaN            NaN                 NaN   

       Book Value per Share Tangible Book per Share Total Debt per Share  \
0                       NaN                     NaN                  NaN   
1                       NaN                     NaN                  NaN   
2                   -20.952                 -38.447               215.31   
3                       NaN                     NaN                  NaN   
4                       NaN                     NaN                  NaN   
...                     ...                     ...                  ...   
317908                  NaN                     NaN                  NaN   
317909                  NaN                     NaN                  Na

#### Разбираемся с пропущенными значениями:

In [7]:
# price_columns = ['Avg.Price Monthly',
#                  'lead_price_1Y', 'lead_price_2Y', 'lead_price_3Y',
#                  'lag_price_1Q', 'lag_price_1H', 'lag_price_3Q', 'lag_price_1Y',
#                  'lag_price_3H', 'lag_price_2Y', 'lag_price_3Y', 'lag_price_5Y',
#                  'price_MA_3', 'price_MA_6', 'price_MA_9', 'price_MA_12',
#                  'price_MA_24', 'price_MA_36', 'price_MA_60',
#                  'min_5Y_price', 'max_5Y_price', 'min_3Y_price', 'max_3Y_price',
#                  'p2lag_price_1Q', 'p2lag_price_1H', 'p2lag_price_3Q', 'p2lag_price_1Y',
#                  'p2lag_price_3H', 'p2lag_price_2Y', 'p2lag_price_3Y', 'p2lag_price_5Y',
#                  'p2min_5Y_price', 'p2max_5Y_price', 'p2min_3Y_price', 'p2max_3Y_price',
#                  'p2price_MA_3', 'p2price_MA_6', 'p2price_MA_9', 'p2price_MA_12',
#                  'p2price_MA_24', 'p2price_MA_36', 'p2price_MA_60'
#                 ]

to_drop_columns = ['rownum', 'Date', 'year',
                   # 'Target_1Y', 'Target_2Y', 'Target_3Y', # убираем простые таргеты
                   # не знаем p - текущую цену, чтобы их вычислить для новых наблюдений
                   'p2lag_price_1Q', 'p2lag_price_1H', 'p2lag_price_3Q', 'p2lag_price_1Y',
                   'p2lag_price_3H', 'p2lag_price_2Y', 'p2lag_price_3Y', 'p2lag_price_5Y',
                   'p2min_5Y_price', 'p2max_5Y_price', 'p2min_3Y_price', 'p2max_3Y_price',
                   'p2price_MA_3', 'p2price_MA_6', 'p2price_MA_9', 'p2price_MA_12',
                   'p2price_MA_24', 'p2price_MA_36', 'p2price_MA_60',
                   # не знаем будущие цены, чтобы вычислить
                   'lead_price_1Y', 'lead_price_2Y', 'lead_price_3Y'                  
                  ]

leak_columns = ['Avg.Price Monthly']

other = ['ticker', 'period', 'isDirect', 'Target_1Y', 'Target_2Y', 'Target_3Y',]
# add year, month, some flags
# encode isDirect

price_columns = ['Avg.Price Monthly',
                 'lag_price_1Q', 'lag_price_1H', 'lag_price_3Q', 'lag_price_1Y',
                 'lag_price_3H', 'lag_price_2Y', 'lag_price_3Y', 'lag_price_5Y',
                 'price_MA_3', 'price_MA_6', 'price_MA_9', 'price_MA_12',
                 'price_MA_24', 'price_MA_36', 'price_MA_60',
                 'min_5Y_price', 'max_5Y_price', 'min_3Y_price', 'max_3Y_price'
                ]

fin_stat_cols = list(set(new_df.columns) - set(to_drop_columns) - set(other) - set(price_columns))

In [8]:
fin_stat_cols

['Total Long-Term Assets',
 'PS Ratio_lag12',
 'Tangible Book per Share_lag18',
 'Net Income_perc3',
 'Shares Outstanding (Basic Average)_lag3',
 'Total Assets',
 'Inventory Turnover_lag18',
 'Cash Ratio_lag3',
 'Equity-to-Asset_lag12',
 'EPS without NRI_lag18',
 'WACC %_lag24',
 'Dividend Yield %_lag3',
 'Price-to-Free-Cash-Flow_lag9',
 'Capital Expenditure_lag24',
 'Total Long-Term Liabilities_lag18',
 'Total Current Assets_lag24',
 'Beta_lag9',
 'EBITDA_lag18',
 'Issuance of Debt',
 'Price-to-Tangible-Book_lag18',
 'Graham Number_lag12',
 'Change In Working Capital_lag18',
 'Issuance of Stock',
 'EPS without NRI',
 'Dividend-Payout-to-FFO_lag18',
 'Inventory-to-Revenue',
 'Change In Inventory_lag3',
 'Tangible Book per Share_lag24',
 'Net Interest Margin (Bank Only) %_lag18',
 'Fees and Other Income_lag6',
 'Days Inventory_lag24',
 'Interest Coverage_lag12',
 'Operating Margin %_lag3',
 'Owner Earnings per Share (TTM)_lag9',
 'Net-Net Working Capital_lag9',
 'YoY EPS Growth_lag6',
 

In [9]:
%%time
new_df = new_df.drop(axis=1, columns=to_drop_columns)

# сначала пропуски в фичах из цены
new_df[price_columns] = new_df.groupby('ticker', sort=False)[price_columns].ffill()
new_df = new_df.dropna(axis=0, subset=['Avg.Price Monthly'])
new_df[price_columns] = new_df.groupby('ticker', sort=False)[price_columns].bfill()


CPU times: user 17.5 s, sys: 58.2 s, total: 1min 15s
Wall time: 1min 47s


In [10]:
%%time

# дальше пропуски в фичах из отчетности
new_df[fin_stat_cols] = new_df.groupby('ticker', sort=False)[fin_stat_cols].ffill()

CPU times: user 45.7 s, sys: 1min 52s, total: 2min 38s
Wall time: 3min 38s


In [11]:
n_nans = new_df[fin_stat_cols].isna().sum().sort_values()
pd.DataFrame(n_nans).T

Short-Term Debt & Capital Lease Obligation  EV-to-Revenue  \
0                                       58292          58292   

   Forward Rate of Return (Yacktman) %  Intangible Assets  \
0                                58292              58292   

   Repurchase of Stock  Capex-to-Revenue  Price-to-Owner-Earnings  \
0                58292             58292                    58292   

   Peter Lynch Fair Value  Graham Number  Sale Of Business  \
0                   58292          58292             58292   

   Net-Net Working Capital  PB Ratio  Cash per Share  \
0                    58292     58292           58292   

   Owner Earnings per Share (TTM)  Dividend Yield %  Net Margin %  Revenue  \
0                           58292             58292         58292    58292   

   Purchase Of Business  Earnings Yield (Joel Greenblatt) %  \
0                 58292                               58292   

   Change In Working Capital  Goodwill  Enterprise Value ($M)  \
0                      58292     58292                  58292   

   Property, Plant and Equipment  ind_template  Book Value per Share  \
0                          58292         58292                 58292   

   Earnings Power Value (EPV)  Payments of Debt   Beta  WACC %  \
0                       58292             58292  58292   58292   

   Median PS Value  Dividends per Share  Forex Rate  Interest Income  \
0            58292                58292       58292            58292   

   Free Cash Flow  Intrinsic Value: Projected FCF  Total Receivables  \
0           58292                           58292              58292   

   Capital Expenditure  Equity-to-Asset  Shares Outstanding (Basic Average)  \
0                58292            58292                               58292   

   Accounts Receivable  Price-to-Operating-Cash-Flow  \
0                58292                         58292   

   Other Income (Minority Interest)  EPS without NRI  Total Assets  \
0                             58292            58292         58292   

   EPS (Basic)  Liabilities-to-Assets  \
0        58292                  58292   

   Long-Term Debt & Capital Lease Obligation  Cash Flow from Operations  \
0                                      58292                      58292   

   Issuance of Debt  Buyback Yield %   REIT  Net Change in Cash  \
0             58292            58292  58292               58292   

   YoY EPS Growth  EPS (Diluted)  Issuance of Stock  Change In Inventory  \
0           58292          58292              58292                58292   

   Tax Rate %  YoY Rev. per Sh. Growth  Net Income  Price-to-Tangible-Book  \
0       58292                    58292       58292                   58292   

   Net Income (Continuing Operations)  Selling, General, & Admin. Expense  \
0                               58292                               58292   

   Asset Turnover  Earnings per Share (Diluted)  ROIC %  \
0           58292                         58292   58292   

   Net Income From Continuing Operations  PEG Ratio  \
0                                  58292      58292   

   Operating Cash Flow per Share  Scaled Net Operating Assets  Sloan Ratio %  \
0                          58292                        58292          58307   

   Total Debt per Share  Tangible Book per Share  Free Cash Flow per Share  \
0                 58337                    58337                     58343   

   Shares Outstanding (Diluted Average)  Revenue per Share  PS Ratio  \
0                                 58343              58343     58471   

   Shiller PE Ratio  Beneish M-Score  Price-to-Free-Cash-Flow  Market Cap  \
0             58471            58471                    58471       58733   

   ROA %  Return-on-Tangible-Asset  Debt-to-Asset  Debt-to-Equity  \
0  58945                     58945          59065           59065   

   Total Equity  Total Liabilities  Net Cash per Share  \
0         59068              59071               59116   

   Net Current Asset Value  Goodwill_lag

In [12]:
# отсекаем фичи, где много пропусков
bad_fin_stat = n_nans[n_nans > 150000].index
good_fin_stat = list(set(fin_stat_cols) - set(bad_fin_stat))
len(good_fin_stat), len(bad_fin_stat), len(fin_stat_cols)

(968, 133, 1101)

In [13]:
%%time

# удаляем показатели где много nan (19 фичей отчетности с их лагами)
new_df = new_df.drop(bad_fin_stat, axis=1)

CPU times: user 7.85 s, sys: 28.6 s, total: 36.5 s
Wall time: 51.4 s


In [14]:
%%time

# отсекаем строки с пропусками в начале для каждого тикера
new_df_copy = new_df[new_df[good_fin_stat].isna().sum(axis=1) < len(good_fin_stat)].copy()
new_df_copy

CPU times: user 26.6 s, sys: 1min 8s, total: 1min 34s
Wall time: 2min 8s


ticker     period ind_template REIT         isDirect Revenue per Share  \
2         AAL 2005-12-01            N    N  Indirect Method            79.612   
3         AAL 2006-01-01            N    N              NaN            79.612   
4         AAL 2006-02-01            N    N              NaN            79.612   
5         AAL 2006-03-01            N    N  Indirect Method            76.205   
6         AAL 2006-04-01            N    N              NaN            76.205   
...       ...        ...          ...  ...              ...               ...   
317908   ZYNE 2021-07-01            N    N              NaN               0.0   
317909   ZYNE 2021-08-01            N    N              NaN               0.0   
317910   ZYNE 2021-09-01            N    N              NaN               0.0   
317911   ZYNE 2021-10-01            N    N              NaN               0.0   
317912   ZYNE 2021-11-01            N    N              NaN               0.0   

       Earnings per Share (Diluted) EPS without NRI  \
2                            -9.639          -9.639   
3                            -9.639          -9.639   
4                            -9.639          -9.639   
5                            -1.312          -1.312   
6                            -1.312          -1.312   
...                             ...             ...   
317908                        -0.25           -0.25   
317909                        -0.25           -0.25   
317910                        -0.25           -0.25   
317911                        -0.25           -0.25   
317912                        -0.25           -0.25   

       Owner Earnings per Share (TTM) Free Cash Flow per Share  \
2                              -3.918                   -1.587   
3                              -3.918                   -1.587   
4                              -3.918                   -1.587   
5                              -1.223                    9.768   
6                              -1.223                    9.768   
...                               ...                      ...   
317908                         -1.028                   -0.182   
317909                         -1.028                   -0.182   
317910                         -1.028                   -0.182   
317911                         -1.028                   -0.182   
317912                         -1.028                   -0.182   

       Operating Cash Flow per Share Cash per Share Dividends per Share  \
2                             -0.123         55.882                 0.0   
3                             -0.123         55.882                 0.0   
4                             -0.123         55.882                 0.0   
5                             11.251         60.337                 0.0   
6                             11.251         60.337                 0.0   
...                              ...            ...                 ...   
317908                        -0.182          2.079                 0.0   
317909                        -0.182          2.079                 0.0   
317910                        -0.182          2.079                 0.0   
317911                        -0.182          2.079                 0.0   
317912                        -0.182          2.079                 0.0   

       Book Value per Share Tangible Book per Share Total Debt per Share  \
2                   -20.952                 -38.447               215.31   
3                   -20.952                 -38.447               215.31   
4                   -20.952                 -38.447               215.31   
5                   -17.982                 -34.777              202.866   
6                   -17.982                 -34.777              202.866   
...                     ...                     ...                  ...   
317908                2.126                   2.126                0.016   
317909                2.126                   2.126                0.01

In [15]:
%%time

# дозаполняем пропуски в обратную сторону:
fin_stat_cols = good_fin_stat
new_df_copy[fin_stat_cols] = new_df_copy.groupby('ticker', sort=False)[fin_stat_cols].bfill()

CPU times: user 31.8 s, sys: 1min 10s, total: 1min 42s
Wall time: 2min 20s


In [16]:
# чтобы отличать месяца подачи отчетности:
new_df_copy['isDirect'].fillna('miss', inplace=True)

In [18]:
n_nans = new_df_copy.isna().sum().sort_values()
pd.DataFrame(n_nans).T

ticker  price_MA_3  isDirect  Avg.Price Monthly  period  lag_price_1Q  \
0       0           0         0                  0       0            15   

   Forex Rate_lag9  Goodwill_lag9  Intangible Assets_lag9  \
0               34             34                      34   

   Property, Plant and Equipment_lag9  Total Receivables_lag9  \
0                                  34                      34   

   Accounts Receivable_lag9  EPS (Diluted)_lag9  EPS (Basic)_lag9  \
0                        34                  34                34   

   Other Income (Minority Interest)_lag9  \
0                                     34   

   Net Income (Continuing Operations)_lag9  Tax Rate %_lag9  \
0                                       34               34   

   Selling, General, & Admin. Expense_lag9  Interest Income_lag9  \
0                                       34                    34   

   Capex-to-Revenue_lag9  Asset Turnover_lag9  Liabilities-to-Assets_lag9  \
0                     34                   34                          34   

   Equity-to-Asset_lag9  Net Margin %_lag9  WACC %_lag9  ROIC %_lag9  \
0                    34                 34           34           34   

   Book Value per Share_lag9  Dividends per Share_lag9  \
0                         34                        34   

   Operating Cash Flow per Share_lag9  YoY EPS Growth_lag9  \
0                                  34                   34   

   Earnings per Share (Diluted)_lag9  \
0                                 34   

   Short-Term Debt & Capital Lease Obligation_lag9  \
0                                               34   

   Long-Term Debt & Capital Lease Obligation_lag9  EPS without NRI_lag9  \
0                                              34                    34   

   Cash per Share_lag9  Net-Net Working Capital_lag9  \
0                   34                            34   

   Enterprise Value ($M)_lag9  Sloan Ratio %_lag9  Buyback Yield %_lag9  \
0                          34                  34                    34   

   Forward Rate of Return (Yacktman) %_lag9  \
0                                        34   

   Earnings Yield (Joel Greenblatt) %_lag9  EV-to-Revenue_lag9  \
0                                       34                  34   

   PEG Ratio_lag9  YoY Rev. per Sh. Growth_lag9  \
0              34                            34   

   Price-to-Operating-Cash-Flow_lag9  Price-to-Tangible-Book_lag9  \
0                                 34                           34   

   PB Ratio_lag9  Graham Number_lag9  Price-to-Owner-Earnings_lag9  \
0             34                  34                            34   

   Capital Expenditure_lag9  Net Change in Cash_lag9  Payments of Debt_lag9  \
0                        34                       34                     34   

   Issuance of Debt_lag9  Repurchase of Stock_lag9  Issuance of Stock_lag9  \
0                     34                        34                      34   

   Sale Of Business_lag9  Purchase Of Business_lag9  \
0                     34                         34   

   Cash Flow from Operations_lag9  Change In Working Capital_lag9  \
0                              34                              34   

   Change In Inventory_lag9  Net Income From Continuing Operations_lag9  \
0                        34                                          34   

   Free Cash Flow_lag9  Scaled Net Operating Assets_lag9  Total Equity_lag9  \
0                   34                                34                 55   

   Total Liabilities_lag9  Return-on-Tangible-Asset_lag9  Debt-to-Equity_lag9  \
0                      55                             55                   55   

   ROA %_lag9  Debt-to-Asset_lag9  \
0          55                  55   

   Short-Term Debt & Capital Lease Obligation_lag6  Goodwill_lag6  \
0                                               58             58   

   Intangible Assets_lag6  Property, Plant and Equipment_lag6  \
0                      58   

In [19]:
# вторая итерация убрать фичи с большим количеством пропусков:
bad_feat = n_nans[n_nans > 38000].index
bad_feat = list(set(bad_feat) - set(other))
good_feat = list(set(new_df_copy.columns) - set(bad_feat))
len(good_feat), len(bad_feat), len(new_df_copy.columns)

(707, 287, 994)

In [20]:
%%time

# удаляем показатели где много nan (41 фича отчетности с их лагами)
new_df_copy = new_df_copy.drop(bad_feat, axis=1)

CPU times: user 3.13 s, sys: 10.8 s, total: 13.9 s
Wall time: 20.2 s


In [21]:
n_nans = new_df_copy.isna().sum().sort_values()
pd.DataFrame(n_nans).T

ticker  price_MA_3  isDirect  Avg.Price Monthly  period  lag_price_1Q  \
0       0           0         0                  0       0            15   

   Forex Rate_lag9  Intangible Assets_lag9  \
0               34                      34   

   Property, Plant and Equipment_lag9  Total Receivables_lag9  \
0                                  34                      34   

   Accounts Receivable_lag9  EPS (Diluted)_lag9  EPS (Basic)_lag9  \
0                        34                  34                34   

   Other Income (Minority Interest)_lag9  \
0                                     34   

   Net Income (Continuing Operations)_lag9  Tax Rate %_lag9  \
0                                       34               34   

   Selling, General, & Admin. Expense_lag9  Interest Income_lag9  \
0                                       34                    34   

   Capex-to-Revenue_lag9  Asset Turnover_lag9  Liabilities-to-Assets_lag9  \
0                     34                   34                          34   

   Equity-to-Asset_lag9  Net Margin %_lag9  WACC %_lag9  ROIC %_lag9  \
0                    34                 34           34           34   

   Book Value per Share_lag9  Dividends per Share_lag9  Cash per Share_lag9  \
0                         34                        34                   34   

   Operating Cash Flow per Share_lag9  EPS without NRI_lag9  \
0                                  34                    34   

   Earnings per Share (Diluted)_lag9  Goodwill_lag9  \
0                                 34             34   

   Short-Term Debt & Capital Lease Obligation_lag9  \
0                                               34   

   Net Income From Continuing Operations_lag9  Change In Inventory_lag9  \
0                                          34                        34   

   YoY Rev. per Sh. Growth_lag9  Buyback Yield %_lag9  Sloan Ratio %_lag9  \
0                            34                    34                  34   

   Scaled Net Operating Assets_lag9  Graham Number_lag9  \
0                                34                  34   

   Net-Net Working Capital_lag9  Enterprise Value ($M)_lag9  \
0                            34                          34   

   Forward Rate of Return (Yacktman) %_lag9  \
0                                        34   

   Earnings Yield (Joel Greenblatt) %_lag9  EV-to-Revenue_lag9  \
0                                       34                  34   

   PEG Ratio_lag9  Price-to-Operating-Cash-Flow_lag9  \
0              34                                 34   

   Price-to-Tangible-Book_lag9  PB Ratio_lag9  Price-to-Owner-Earnings_lag9  \
0                           34             34                            34   

   Free Cash Flow_lag9  Capital Expenditure_lag9  Net Change in Cash_lag9  \
0                   34                        34                       34   

   Payments of Debt_lag9  Issuance of Debt_lag9  Repurchase of Stock_lag9  \
0                     34                     34                        34   

   Issuance of Stock_lag9  Sale Of Business_lag9  Purchase Of Business_lag9  \
0                      34                     34                         34   

   Cash Flow from Operations_lag9  YoY EPS Growth_lag9  \
0                              34                   34   

   Change In Working Capital_lag9  \
0                              34   

   Long-Term Debt & Capital Lease Obligation_lag9  ROA %_lag9  \
0                                              34          55   

   Total Equity_lag9  Return-on-Tangible-Asset_lag9  Total Liabilities_lag9  \
0                 55                             55                      55   

   Debt-to-Asset_lag9  Debt-to-Equity_lag9  Book Value per Share_lag6  \
0                  55                   55                         58   

   Long-Term Debt & Capital Lease Obligation_lag6  \
0                                              58   

   Net Income From Continuing Operations_lag6  Change In Inventory_lag6

In [21]:
# остались пропуски, но от них избавимся позже, после расчета таргета

#### Добавляем индустрию и месяц/год:

In [22]:
new_df_copy['year'] = pd.DatetimeIndex(new_df_copy['period']).year
new_df_copy['month'] = pd.DatetimeIndex(new_df_copy['period']).month

In [23]:
new_df_copy

ticker     period ind_template REIT         isDirect Revenue per Share  \
2         AAL 2005-12-01            N    N  Indirect Method            79.612   
3         AAL 2006-01-01            N    N             miss            79.612   
4         AAL 2006-02-01            N    N             miss            79.612   
5         AAL 2006-03-01            N    N  Indirect Method            76.205   
6         AAL 2006-04-01            N    N             miss            76.205   
...       ...        ...          ...  ...              ...               ...   
317908   ZYNE 2021-07-01            N    N             miss               0.0   
317909   ZYNE 2021-08-01            N    N             miss               0.0   
317910   ZYNE 2021-09-01            N    N             miss               0.0   
317911   ZYNE 2021-10-01            N    N             miss               0.0   
317912   ZYNE 2021-11-01            N    N             miss               0.0   

       Earnings per Share (Diluted) EPS without NRI  \
2                            -9.639          -9.639   
3                            -9.639          -9.639   
4                            -9.639          -9.639   
5                            -1.312          -1.312   
6                            -1.312          -1.312   
...                             ...             ...   
317908                        -0.25           -0.25   
317909                        -0.25           -0.25   
317910                        -0.25           -0.25   
317911                        -0.25           -0.25   
317912                        -0.25           -0.25   

       Owner Earnings per Share (TTM) Free Cash Flow per Share  \
2                              -3.918                   -1.587   
3                              -3.918                   -1.587   
4                              -3.918                   -1.587   
5                              -1.223                    9.768   
6                              -1.223                    9.768   
...                               ...                      ...   
317908                         -1.028                   -0.182   
317909                         -1.028                   -0.182   
317910                         -1.028                   -0.182   
317911                         -1.028                   -0.182   
317912                         -1.028                   -0.182   

       Operating Cash Flow per Share Cash per Share Dividends per Share  \
2                             -0.123         55.882                 0.0   
3                             -0.123         55.882                 0.0   
4                             -0.123         55.882                 0.0   
5                             11.251         60.337                 0.0   
6                             11.251         60.337                 0.0   
...                              ...            ...                 ...   
317908                        -0.182          2.079                 0.0   
317909                        -0.182          2.079                 0.0   
317910                        -0.182          2.079                 0.0   
317911                        -0.182          2.079                 0.0   
317912                        -0.182          2.079                 0.0   

       Book Value per Share Tangible Book per Share Total Debt per Share  \
2                   -20.952                 -38.447               215.31   
3                   -20.952                 -38.447               215.31   
4                   -20.952                 -38.447               215.31   
5                   -17.982                 -34.777              202.866   
6                   -17.982                 -34.777              202.866   
...                     ...                     ...                  ...   
317908                2.126                   2.126                0.016   
317909                2.126                   2.126                0.01

In [24]:
nasdaq = pd.read_csv('КР/nasdaq_screener_1636828053632.csv', sep=',')
nasdaq

Symbol                                               Name Last Sale  \
0         A             Agilent Technologies Inc. Common Stock   $160.88   
1        AA                    Alcoa Corporation Common Stock     $51.92   
2       AAC  Ares Acquisition Corporation Class A Ordinary ...     $9.85   
3      AACG   ATA Creativity Global American Depositary Shares     $2.21   
4      AACI            Armada Acquisition Corp. I Common Stock     $9.75   
...     ...                                                ...       ...   
8142    ZWS      Zurn Water Solutions Corporation Common Stock    $37.46   
8143     ZY                         Zymergen Inc. Common Stock    $10.26   
8144   ZYME                       Zymeworks Inc. Common Shares    $20.15   
8145   ZYNE          Zynerba Pharmaceuticals Inc. Common Stock     $4.28   
8146   ZYXI                            Zynex Inc. Common Stock    $14.60   

      Net Change_perc   Change    Market Cap        Country  IPO Year  \
0                2.09    1.316  4.870202e+10  United States    1999.0   
1                0.71    1.386  9.714395e+09            NaN    2016.0   
2                0.01    0.102  1.231250e+09            NaN    2021.0   
3                0.00    0.000  6.934299e+07          China       NaN   
4               -0.03   -0.307  2.019176e+08  United States    2021.0   
...               ...      ...           ...            ...       ...   
8142             0.46    1.243  4.545753e+09  United States    2012.0   
8143            -0.38   -3.571  1.050520e+09  United States    2021.0   
8144             0.30    1.511  9.380624e+08         Canada    2017.0   
8145             0.36    9.184  1.765566e+08  United States    2015.0   
8146            -0.02   -0.137  5.077835e+08  United States       NaN   

       Volume            Sector  \
0     1444785     Capital Goods   
1     9303887  Basic Industries   
2      464622           Finance   
3        7823     Miscellaneous   
4      943316               NaN   
...       ...               ...   
8142  1443075  Public Utilities   
8143   539718  Basic Industries   
8144   760485               NaN   
8145  4323929       Health Care   
8146   220660       Health Care   

                                               Industry  
0                                   Electrical Products  
1                                    Metal Fabrications  
2                                     Business Services  
3                        Service to the Health Industry  
4                                                   NaN  
...                                                 ...  
8142                                       Water Supply  
8143                             Industrial Specialties  
8144                                                NaN  
8145         Biotechnology: Pharmaceutical Preparations  
8146  Biotechnology: Electromedical  and  Electrothe...  

[8147 rows x 11 columns]

In [25]:
nasdaq_join = nasdaq[['Symbol', 'Industry']].copy()
nasdaq_join.columns = ['ticker', 'Industry']
nasdaq_join

ticker                                           Industry
0         A                                Electrical Products
1        AA                                 Metal Fabrications
2       AAC                                  Business Services
3      AACG                     Service to the Health Industry
4      AACI                                                NaN
...     ...                                                ...
8142    ZWS                                       Water Supply
8143     ZY                             Industrial Specialties
8144   ZYME                                                NaN
8145   ZYNE         Biotechnology: Pharmaceutical Preparations
8146   ZYXI  Biotechnology: Electromedical  and  Electrothe...

[8147 rows x 2 columns]

In [26]:
nasdaq_join.ticker.nunique()

8147

In [57]:
df_final = new_df_copy.merge(nasdaq_join, how='left', on='ticker')
df_final

ticker     period ind_template REIT         isDirect Revenue per Share  \
0         AAL 2005-12-01            N    N  Indirect Method            79.612   
1         AAL 2006-01-01            N    N             miss            79.612   
2         AAL 2006-02-01            N    N             miss            79.612   
3         AAL 2006-03-01            N    N  Indirect Method            76.205   
4         AAL 2006-04-01            N    N             miss            76.205   
...       ...        ...          ...  ...              ...               ...   
257202   ZYNE 2021-07-01            N    N             miss               0.0   
257203   ZYNE 2021-08-01            N    N             miss               0.0   
257204   ZYNE 2021-09-01            N    N             miss               0.0   
257205   ZYNE 2021-10-01            N    N             miss               0.0   
257206   ZYNE 2021-11-01            N    N             miss               0.0   

       Earnings per Share (Diluted) EPS without NRI  \
0                            -9.639          -9.639   
1                            -9.639          -9.639   
2                            -9.639          -9.639   
3                            -1.312          -1.312   
4                            -1.312          -1.312   
...                             ...             ...   
257202                        -0.25           -0.25   
257203                        -0.25           -0.25   
257204                        -0.25           -0.25   
257205                        -0.25           -0.25   
257206                        -0.25           -0.25   

       Owner Earnings per Share (TTM) Free Cash Flow per Share  \
0                              -3.918                   -1.587   
1                              -3.918                   -1.587   
2                              -3.918                   -1.587   
3                              -1.223                    9.768   
4                              -1.223                    9.768   
...                               ...                      ...   
257202                         -1.028                   -0.182   
257203                         -1.028                   -0.182   
257204                         -1.028                   -0.182   
257205                         -1.028                   -0.182   
257206                         -1.028                   -0.182   

       Operating Cash Flow per Share Cash per Share Dividends per Share  \
0                             -0.123         55.882                 0.0   
1                             -0.123         55.882                 0.0   
2                             -0.123         55.882                 0.0   
3                             11.251         60.337                 0.0   
4                             11.251         60.337                 0.0   
...                              ...            ...                 ...   
257202                        -0.182          2.079                 0.0   
257203                        -0.182          2.079                 0.0   
257204                        -0.182          2.079                 0.0   
257205                        -0.182          2.079                 0.0   
257206                        -0.182          2.079                 0.0   

       Book Value per Share Tangible Book per Share Total Debt per Share  \
0                   -20.952                 -38.447               215.31   
1                   -20.952                 -38.447               215.31   
2                   -20.952                 -38.447               215.31   
3                   -17.982                 -34.777              202.866   
4                   -17.982                 -34.777              202.866   
...                     ...                     ...                  ...   
257202                2.126                   2.126                0.016   
257203                2.126                   2.126                0.01

In [58]:
df_final['Industry'] = df_final['Industry'].fillna('Unknown industry')
df_final[['ind_template','REIT']] = df_final[['ind_template','REIT']].fillna('Missed')

In [59]:
df_final.ind_template.unique(), df_final.REIT.unique(), df_final.isDirect.unique()

(array(['N', 'Missed', 'B', 'I'], dtype=object),
 array(['N', 'Missed', 'Y'], dtype=object),
 array(['Indirect Method', 'miss'], dtype=object))

In [60]:
df_final['isDirect'] = np.where(df_final['isDirect'] == 'Indirect Method', 1, 0)

#### Добавляем таргеты:

In [62]:
df_final['lead_price_1Q'] = df_final.groupby('ticker')['Avg.Price Monthly'].shift(-3)
df_final['lead_price_1Q'] = np.where(df_final['lead_price_1Q'] == 0,
                                     np.nan,
                                     df_final['lead_price_1Q']
                                    )
df_final['Avg.Price Monthly'] = np.where(df_final['Avg.Price Monthly'] == 0,
                                         np.nan,
                                         df_final['Avg.Price Monthly']
                                        )

df_final['return_Q_forward'] = df_final['lead_price_1Q'] / df_final['Avg.Price Monthly'] - 1

In [63]:
%%time

x = np.array([0.25, 0.5, 1, 1.5, 2])
qs = (4 * x).astype(int)
eps = [0.01, 0.05]

for e in eps:
    for q in qs:
        lags = 3 * np.arange(0, q)
        names = [f'ret_Q_{i+3}_months_fwd' for i in lags]
        for name, lag in zip(names, lags):
            df_final[name] = df_final.groupby('ticker')['return_Q_forward'].shift(-lag)
        # ставим таргет для растущих бумаг
        df_final[f'min_ret_Q{q}_{e}'] = np.where(df_final[names].isna().sum(axis=1) == 0,
                                                 df_final[names].min(axis=1),
                                                 -1
                                                )
        df_final[f'target_more_{e}_in_{q}_quart_along'] = np.where(df_final[f'min_ret_Q{q}_{e}'] <= -1,
                                                                   np.nan,
                                                                   np.where(df_final[f'min_ret_Q{q}_{e}'] > e,
                                                                            1,
                                                                            0)
                                                                  )
        # ставим таргет для падающих бумаг
        df_final[f'max_ret_Q{q}_{e}'] = np.where(df_final[names].isna().sum(axis=1) == 0,
                                                 df_final[names].max(axis=1),
                                                 np.inf
                                                )
        df_final[f'target_less_{-e}_in_{q}_quart_along'] = np.where(df_final[f'max_ret_Q{q}_{e}'] == np.inf,
                                                                    np.nan,
                                                                    np.where(df_final[f'max_ret_Q{q}_{e}'] < -e,
                                                                             1,
                                                                             0)
                                                                   )
        df_final = df_final.drop(axis=1, columns=names+[f'min_ret_Q{q}_{e}', f'max_ret_Q{q}_{e}'])
        

CPU times: user 1min 5s, sys: 43.2 s, total: 1min 49s
Wall time: 2min 8s


In [64]:
eps_1 = [0.15, 0.3]
eps_2 = [0.25, 0.5]
eps_3 = 0.6
for e in eps_1:
    df_final[f'return_1Y_more_{e}'] = np.where(df_final['Target_1Y'] > e, 1, 0)
    df_final[f'return_1Y_less_{-e}'] = np.where(df_final['Target_1Y'] < -e, 1, 0)
    
for e in eps_2:
    df_final[f'return_2Y_more_{e}'] = np.where(df_final['Target_2Y'] > e, 1, 0)
    df_final[f'return_2Y_less_{-e}'] = np.where(df_final['Target_2Y'] < -e, 1, 0)
    
df_final[f'return_3Y_more_{eps_3}'] = np.where(df_final['Target_3Y'] > eps_3, 1, 0)
df_final[f'return_3Y_less_{-eps_3}'] = np.where(df_final['Target_3Y'] < -eps_3, 1, 0)

df_final['return_1Y'] = df_final['Target_1Y']
df_final['return_2Y'] = df_final['Target_2Y']
df_final['return_3Y'] = df_final['Target_3Y']
df_final['price'] = df_final['Avg.Price Monthly']
    
df_final = df_final.drop(['lead_price_1Q', 'return_Q_forward', 'Avg.Price Monthly', 
                          'Target_1Y', 'Target_2Y', 'Target_3Y'], axis=1)

#### Заполняем оставшиеся пропуски в фичах:

In [65]:
%%time
df_final[df_final.columns[:-34]] = df_final[df_final.columns[:-34]].fillna(0)
df_final

CPU times: user 10min 7s, sys: 3min 27s, total: 13min 35s
Wall time: 13min 55s


ticker     period ind_template REIT  isDirect  Revenue per Share  \
0         AAL 2005-12-01            N    N         1             79.612   
1         AAL 2006-01-01            N    N         0             79.612   
2         AAL 2006-02-01            N    N         0             79.612   
3         AAL 2006-03-01            N    N         1             76.205   
4         AAL 2006-04-01            N    N         0             76.205   
...       ...        ...          ...  ...       ...                ...   
257202   ZYNE 2021-07-01            N    N         0              0.000   
257203   ZYNE 2021-08-01            N    N         0              0.000   
257204   ZYNE 2021-09-01            N    N         0              0.000   
257205   ZYNE 2021-10-01            N    N         0              0.000   
257206   ZYNE 2021-11-01            N    N         0              0.000   

        Earnings per Share (Diluted)  EPS without NRI  \
0                             -9.639           -9.639   
1                             -9.639           -9.639   
2                             -9.639           -9.639   
3                             -1.312           -1.312   
4                             -1.312           -1.312   
...                              ...              ...   
257202                        -0.250           -0.250   
257203                        -0.250           -0.250   
257204                        -0.250           -0.250   
257205                        -0.250           -0.250   
257206                        -0.250           -0.250   

        Owner Earnings per Share (TTM)  Free Cash Flow per Share  \
0                               -3.918                    -1.587   
1                               -3.918                    -1.587   
2                               -3.918                    -1.587   
3                               -1.223                     9.768   
4                               -1.223                     9.768   
...                                ...                       ...   
257202                          -1.028                    -0.182   
257203                          -1.028                    -0.182   
257204                          -1.028                    -0.182   
257205                          -1.028                    -0.182   
257206                          -1.028                    -0.182   

        Operating Cash Flow per Share  Cash per Share  Dividends per Share  \
0                              -0.123          55.882                  0.0   
1                              -0.123          55.882                  0.0   
2                              -0.123          55.882                  0.0   
3                              11.251          60.337                  0.0   
4                              11.251          60.337                  0.0   
...                               ...             ...                  ...   
257202                         -0.182           2.079                  0.0   
257203                         -0.182           2.079                  0.0   
257204                         -0.182           2.079                  0.0   
257205                         -0.182           2.079                  0.0   
257206                         -0.182           2.079                  0.0   

        Book Value per Share  Tangible Book per Share  Total Debt per Share  \
0                    -20.952                  -38.447               215.310   
1                    -20.952                  -38.447               215.310   
2                    -20.952                  -38.447               215.310   
3                    -17.982                  -34.777               202.866   
4                    -17.982                  -34.777               202.866   
...                      ...                      ...                   ...   
257202                 2.126                    2.126                 0.016   
257203                 2.126       

In [66]:
%%time
df_final = df_final.replace([np.inf, -np.inf], 0)

CPU times: user 3.43 s, sys: 4.06 s, total: 7.48 s
Wall time: 8.37 s


In [67]:
n_nans = df_final.isna().sum().sort_values(ascending=False)
pd.DataFrame(n_nans).T

return_3Y  target_more_0.05_in_8_quart_along  \
0      47012                              32271   

   target_more_0.01_in_8_quart_along  target_less_-0.01_in_8_quart_along  \
0                              32271                               32271   

   target_less_-0.05_in_8_quart_along  return_2Y  \
0                               32271      32228   

   target_less_-0.01_in_6_quart_along  target_more_0.01_in_6_quart_along  \
0                               24590                              24590   

   target_more_0.05_in_6_quart_along  target_less_-0.05_in_6_quart_along  \
0                              24590                               24590   

   target_more_0.05_in_4_quart_along  target_less_-0.05_in_4_quart_along  \
0                              16781                               16781   

   target_more_0.01_in_4_quart_along  target_less_-0.01_in_4_quart_along  \
0                              16781                               16781   

   return_1Y  target_less_-0.05_in_2_quart_along  \
0      16740                                8643   

   target_more_0.05_in_2_quart_along  target_less_-0.01_in_2_quart_along  \
0                               8643                                8643   

   target_more_0.01_in_2_quart_along  target_more_0.05_in_1_quart_along  \
0                               8643                               4385   

   target_less_-0.05_in_1_quart_along  target_more_0.01_in_1_quart_along  \
0                                4385                               4385   

   target_less_-0.01_in_1_quart_along  price  \
0                                4385     33   

   Earnings Yield (Joel Greenblatt) %_lag12  YoY EPS Growth_lag12  \
0                                         0                     0   

   Earnings Power Value (EPV)_lag12  Piotroski F-Score_lag12  \
0                                 0                        0   

   Beneish M-Score_lag12  Scaled Net Operating Assets_lag12  \
0                      0                                  0   

   Sloan Ratio %_lag12  Shares Buyback Ratio %_lag12  Buyback Yield %_lag12  \
0                    0                             0                      0   

   YoY Rev. per Sh. Growth_lag12  Shares Outstanding (Basic Average)_lag12  \
0                              0                                         0   

   EV-to-Revenue_lag12  Beta_lag12  Forex Rate_lag12  Revenue per Share_lag18  \
0                    0           0                 0                        0   

   Earnings per Share (Diluted)_lag18  EPS without NRI_lag18  \
0                                   0                      0   

   Owner Earnings per Share (TTM)_lag18  Free Cash Flow per Share_lag18  \
0                                     0                               0   

   Operating Cash Flow per Share_lag18  Graham Number_lag12  \
0                                    0                    0   

   Peter Lynch Fair Value_lag12  Median PS Value_lag12  \
0                             0                      0   

   Intrinsic Value: Projected FCF_lag12  PEG Ratio_lag12  PS Ratio_lag12  \
0                                     0                0               0   

   Price-to-Operating-Cash-Flow_lag12  Price-to-Free-Cash-Flow_lag12  \
0                                   0                              0   

   Price-to-Tangible-Book_lag12  PB Ratio_lag12  \
0                             0               0   

   Price-to-Owner-Earnings_lag12  Dividends per Share_lag18  \
0                              0                          0   

   PE Ratio without NRI_lag12  Forward Rate of Return (Yacktman) %_lag12  \
0                           0                                          0   

   Shiller PE Ratio_lag12  Dividend Yield %_lag12  Market Cap_lag12  \
0                       0                       0                 0   

   Enterprise Value ($M)_lag12  Net Cash per Share_lag12  \
0                            0                         0   

   Net Current Asset Value_l

In [69]:
df_final.shape

(257207, 740)

In [70]:
df_final = df_final.dropna(axis=0, subset=['price'])
df_final.shape

(257174, 740)

In [71]:
df_final.describe()

isDirect  Revenue per Share  Earnings per Share (Diluted)  \
count  257174.000000       2.571740e+05                 257174.000000   
mean        0.324453       2.550325e+02                    -47.276296   
std         0.468171       1.752675e+04                   2144.993762   
min         0.000000      -2.662500e+03                -357051.000000   
25%         0.000000       8.590000e-01                     -0.026000   
50%         0.000000       2.499000e+00                      0.172000   
75%         1.000000       6.595000e+00                      0.490000   
max         1.000000       1.714400e+06                  30585.500000   

       EPS without NRI  Owner Earnings per Share (TTM)  \
count    257174.000000                   257174.000000   
mean        -12.161417                      -38.362804   
std         371.067460                     1222.455072   
min      -52271.600000                  -131259.000000   
25%          -0.030000                       -0.043000   
50%           0.170000                        0.175000   
75%           0.480000                        1.499000   
max       12275.900000                    12413.800000   

       Free Cash Flow per Share  Operating Cash Flow per Share  \
count             257174.000000                  257174.000000   
mean                 -32.265091                     -26.247045   
std                 2154.256943                    2029.918028   
min              -545200.000000                 -519900.000000   
25%                   -0.158000                      -0.015000   
50%                    0.118000                       0.287000   
75%                    0.584000                       0.864000   
max                54400.000000                   92750.000000   

       Cash per Share  Dividends per Share  Book Value per Share  \
count   257174.000000        257174.000000          2.571740e+05   
mean       126.968257             0.174187          2.479902e+02   
std       3424.448768             5.983684          1.422672e+04   
min         -0.757000            -1.598000         -1.688933e+05   
25%          0.350000             0.000000          3.280000e+00   
50%          1.512000             0.000000          8.663000e+00   
75%          4.343000             0.165000          1.716900e+01   
max     439800.000000          1727.990000          1.715550e+06   

       Tangible Book per Share  Total Debt per Share          ROE %  \
count            257174.000000         257174.000000  257174.000000   
mean                -12.973445            155.635169    -167.355866   
std                7052.104097           8140.354594    9374.677052   
min             -733575.000000              0.000000 -724256.667000   
25%                   1.028000              0.249000      -2.213000   
50%                   4.984000              3.646000       8.931000   
75%                  12.374750             12.597000      17.613000   
max              227142.857000         848800.000000  143000.000000   

       ROE % Adjusted to Book Value          ROA %  Return-on-Tangible-Equity  \
count                 257174.000000  257174.000000              257174.000000   
mean                       0.223927     -22.494895                 -88.083362   
std                       97.093966    2715.245148                4515.601226   
min                    -4291.290000 -534000.000000             -954600.000000   
25%                       -0.880000      -0.612000                  -2.266000   
50%                        4.240000       2.670000                  10.667000   
75%                        7.710000       7.860750                  25.603250   
max                    10072.680000  206400.000000              522259.854000   

       Return-on-Tangible-Asset         ROIC %         WACC %  \
count              2.571740e+05  257174.000000  257174.000000   
mean              -2.933837e+01    -163.252006       8.548466   
std                5.056313e+03    6400.848402       9.086

In [72]:
# Пропуски только в таргетах
df_final.to_csv('gross_simple_return_data.csv', sep=',', index=False)

In [73]:
data = pd.read_csv('gross_simple_return_data.csv')
data

ticker      period ind_template REIT  isDirect  Revenue per Share  \
0         AAL  2005-12-01            N    N         1             79.612   
1         AAL  2006-01-01            N    N         0             79.612   
2         AAL  2006-02-01            N    N         0             79.612   
3         AAL  2006-03-01            N    N         1             76.205   
4         AAL  2006-04-01            N    N         0             76.205   
...       ...         ...          ...  ...       ...                ...   
257169   ZYNE  2021-07-01            N    N         0              0.000   
257170   ZYNE  2021-08-01            N    N         0              0.000   
257171   ZYNE  2021-09-01            N    N         0              0.000   
257172   ZYNE  2021-10-01            N    N         0              0.000   
257173   ZYNE  2021-11-01            N    N         0              0.000   

        Earnings per Share (Diluted)  EPS without NRI  \
0                             -9.639           -9.639   
1                             -9.639           -9.639   
2                             -9.639           -9.639   
3                             -1.312           -1.312   
4                             -1.312           -1.312   
...                              ...              ...   
257169                        -0.250           -0.250   
257170                        -0.250           -0.250   
257171                        -0.250           -0.250   
257172                        -0.250           -0.250   
257173                        -0.250           -0.250   

        Owner Earnings per Share (TTM)  Free Cash Flow per Share  \
0                               -3.918                    -1.587   
1                               -3.918                    -1.587   
2                               -3.918                    -1.587   
3                               -1.223                     9.768   
4                               -1.223                     9.768   
...                                ...                       ...   
257169                          -1.028                    -0.182   
257170                          -1.028                    -0.182   
257171                          -1.028                    -0.182   
257172                          -1.028                    -0.182   
257173                          -1.028                    -0.182   

        Operating Cash Flow per Share  Cash per Share  Dividends per Share  \
0                              -0.123          55.882                  0.0   
1                              -0.123          55.882                  0.0   
2                              -0.123          55.882                  0.0   
3                              11.251          60.337                  0.0   
4                              11.251          60.337                  0.0   
...                               ...             ...                  ...   
257169                         -0.182           2.079                  0.0   
257170                         -0.182           2.079                  0.0   
257171                         -0.182           2.079                  0.0   
257172                         -0.182           2.079                  0.0   
257173                         -0.182           2.079                  0.0   

        Book Value per Share  Tangible Book per Share  Total Debt per Share  \
0                    -20.952                  -38.447               215.310   
1                    -20.952                  -38.447               215.310   
2                    -20.952                  -38.447               215.310   
3                    -17.982                  -34.777               202.866   
4                    -17.982                  -34.777               202.866   
...                      ...                      ...                   ...   
257169                 2.126                    2.126                 0.016   
257170                 

In [74]:
pd.DataFrame(data[data.columns[-34:-4]].mean(),
             columns = ['Classes ratio']
            )



Classes ratio
target_more_0.01_in_1_quart_along        0.523807
target_less_-0.01_in_1_quart_along       0.416712
target_more_0.01_in_2_quart_along        0.288002
target_less_-0.01_in_2_quart_along       0.187151
target_more_0.01_in_4_quart_along        0.089774
target_less_-0.01_in_4_quart_along       0.041614
target_more_0.01_in_6_quart_along        0.025991
target_less_-0.01_in_6_quart_along       0.010743
target_more_0.01_in_8_quart_along        0.008171
target_less_-0.01_in_8_quart_along       0.002832
target_more_0.05_in_1_quart_along        0.409161
target_less_-0.05_in_1_quart_along       0.314280
target_more_0.05_in_2_quart_along        0.180408
target_less_-0.05_in_2_quart_along       0.117306
target_more_0.05_in_4_quart_along        0.036548
target_less_-0.05_in_4_quart_along       0.020123
target_more_0.05_in_6_quart_along        0.006556
target_less_-0.05_in_6_quart_along       0.004333
target_more_0.05_in_8_quart_along        0.001378
target_less_-0.05_in_8_quart_along       0.001054
return_1Y_more_0.15                      0.375800
return_1Y_less_-0.15                     0.238889
return_1Y_more_0.3                       0.246549
return_1Y_less_-0.3                      0.137973
return_2Y_more_0.25                      0.348982
return_2Y_less_-0.25                     0.189086
return_2Y_more_0.5                       0.219486
return_2Y_less_-0.5                      0.090814
return_3Y_more_0.6                       0.230610
return_3Y_less_-0.6                      0.073184